<a href="https://colab.research.google.com/github/davies-w/testing/blob/main/holoview_audio_zoom.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>


[Original Idea and Basic Code Colab](https://github.com/scottire/fastpages/blob/master/_notebooks/2020-10-21-interactive-audio-plots-in-jupyter-notebook.ipynb)

[Holoviews](https://holoviews.org/index.html) / [Bokeh](https://bokeh.org/) / [Panel Audio](https://panel.holoviz.org/reference/panes/Audio.html) /
 [Ticks](https://discourse.holoviz.org/t/how-to-label-every-tick-in-x-axis/1986/2)

[Forum Link for this Notebook's Issues](https://discourse.holoviz.org/t/holoview-panel-audio-player/5976)

## Read Me
Based off of Scott's notebook (any errors are mine of course), this is an attempt to make an audio player with two parts:

* A section clickable area, where the playback should jump to the start of the section. It's designed to stay the same size through the playback of the song, so you can simply "jump" to the part you listen to, like an "index".

* A waveform inspection window, where you can click to a precise part of a waveform and listen to it from there. This can also be zoomed with the scroll wheel and panned.

* This should be stand-alone runnable - I'm using an example audio file from Librosa.

## What's not working?

* Sometimes the code just stops working when clicking around. No error messages just stops showing the cursor moving. Sometimes it silently just re-sets and appears to lose the cursor altogether, although audio plays still. This is probably the most annoying feature - I could probably figure out the first two
items myself, but this feels like an internal problem.

* Moving the waveform inspection window to the current timestamp (while keeping same view). This is critical because if you zoom in and then click to a new section, you lose your playback location.

* Waveform inspection window "self-scrolling" if you are zoomed in to a few seconds of window. This zoom level is needed so you can see the waveform precisely.

* Very minor bug, Zoom Out doesn't zoom all the way out for some reason, you have to hit RESET.

* Very, very minor bug, sometimes the playback cursor jumps back one time, then ends up in the right place. I'm assuming this is due to the weirdness of multithreading in Python/Javascript etc.


In [ ]:
!pip install -q librosa

In [ ]:
import holoviews as hv
import panel as pn

from bokeh.models.formatters import DatetimeTickFormatter
from bokeh import models

import librosa
from scipy.signal import decimate
import numpy as np
from IPython.display import display, Markdown, HTML, Javascript, Audio

# Stop any internal scrolling for a cell.
display(Javascript('''google.colab.output.setIframeHeight(0, true, {maxHeight: 5000})'''))

#
# get an audio file to play!
#
filename = librosa.ex('fishin')
y, sr = librosa.load(filename, offset=0.0)

# Load bokeh
hv.extension("bokeh", logo=False)

# running time of song
max_time = y.shape[0]/sr
# Now crudely downsample so we can draw it without going out of ram.
y = decimate(y, 10)
# set up the x axis values, 1 per sample, in milliseconds.
x_time = 1000*np.linspace(0, max_time, y.shape[0])

dateformat =  DatetimeTickFormatter(microseconds = '%M:%S.%1N',
                                    milliseconds = '%M:%S.%1N',
                                    seconds = '%M:%S',
                                    minsec = '%M:%S',
                                    days = '',
                                    months= '',
                                    years='')

#
# Wave Hook Graph Params
#
def wave_hook(plot, element):
    # Control max x zoom in and out.
    x_range = plot.handles['plot'].x_range
    x_range.bounds = (0, max_time*1000)
    x_range.min_interval=500  # smallest zoom in range is 0.5 seconds.

    plot.handles['xaxis'].minor_tick_in = 0
    plot.handles['xaxis'].minor_tick_out = 0
    plot.handles['xaxis'].major_tick_line_color = None

    plot.state.toolbar.logo = None
    plot.state.toolbar.active_drag = None
    plot.state.toolbar.active_inspect = None
    plot.state.toolbar.active_multi = None
    plot.state.toolbar.active_scroll = None
    #plot.state.toolbar.active_tap = None

    for tool in plot.state.toolbar.tools:
      if isinstance(tool, models.tools.BoxZoomTool):
        plot.state.toolbar.tools.remove(tool)

    for tool in plot.state.toolbar.tools:
      if isinstance(tool, models.tools.SaveTool):
        plot.state.toolbar.tools.remove(tool)

wave_tool_list = ["xwheel_zoom", "xpan", "reset"]

wave_curve = hv.Curve((x_time, y), 'time','amp').opts( \
                                                       width=1000,
                                                       height=200,
                                                       padding=(0.0, 0.11),
                                                       color='lawngreen',
                                                       line_width=0.5,
                                                       xticks=15,   # 30, 60
                                                       xformatter=dateformat,
                                                       tools=wave_tool_list,
                                                       active_tools=wave_tool_list,
                                                       default_tools=wave_tool_list,
                                                       hooks = [wave_hook],
                                                       axiswise=True)

#
# Rectangle Params
#
def rect_hook(plot, element):
    # Same as waveform, but also disable WheelZoom and Pan.
    wave_hook(plot, element)

    for tool in plot.state.toolbar.tools:
      if isinstance(tool, models.tools.PanTool):
        plot.state.toolbar.tools.remove(tool)

    for tool in plot.state.toolbar.tools:
      if isinstance(tool, models.tools.WheelZoomTool):
        plot.state.toolbar.tools.remove(tool)

# No tools at all!
rect_tool_list = []

#
# make a sample, evenly spaced set of sections.
# Rects are bottom left, top right coordinates.
# colors are just sequenced 0-9, alpha is 0.1, as I was overlaying on waveform
#, but doesn't matter now.
#
times = np.linspace(0, max_time, 10)
rect_list = [(1000*t1, -1, 1000*t2, 1, t3, 0.1) for t1, t2, t3 in zip(times[:-1], times[1:], range(len(times)-1))]


rect_patches = hv.Rectangles(rect_list, kdims=['x','y', 'x1', 'y1'], vdims=['value','alpha']).opts( \
                                                       color='value',
                                                       alpha='alpha',
                                                       cmap='Spectral',
                                                       padding=0.0,
                                                       width=1000,
                                                       height=75,
                                                       xticks=0,
                                                       yticks=0,
                                                       xformatter=dateformat,
                                                       tools=rect_tool_list,
                                                       active_tools=rect_tool_list,
                                                       default_tools=rect_tool_list,
                                                       hooks = [rect_hook]).redim.label(x=' ', y=' ')



audio = pn.pane.Audio(filename, sample_rate=sr, name='audio', throttle=1000, autoplay=False)

#
# waveform updater
#
def update_playhead_wave(x, y, t, *arg):
    if x is None and t is not None:
        return hv.VLine(t*1000).opts(line_width=1, color='red')
    if x is not None:
        audio.time = x/1000
        audio.paused = False
        return hv.VLine(x).opts(line_width=1, color='red')
    return hv.VLine(100).opts(line_width=1, color='red')

tap_stream_wave = hv.streams.Tap(transient=True) # was single
time_play_stream_wave = hv.streams.Params(parameters=[audio.param.time], rename={'time': 't'})
dmap_time_wave = hv.DynamicMap(update_playhead_wave, streams=[tap_stream_wave, time_play_stream_wave])

#
# section rectangles updater
#
def update_playhead_rect(x, y, t, *arg):
    if x is None and t is not None:
        return hv.VLine(t*1000).opts(line_width=1, color='red')
    if x is not None:
        for clip_value in reversed(rect_list):
          if clip_value[0] < x:
            break
        audio.time = clip_value[0]/1000
        audio.paused = False
        return hv.VLine(clip_value[0]).opts(line_width=1, color='red')
    return hv.VLine(100).opts(line_width=1, color='red')

tap_stream_rect = hv.streams.Tap(transient=True) # was single
time_play_stream_rect = hv.streams.Params(parameters=[audio.param.time], rename={'time': 't'})
dmap_time_rect = hv.DynamicMap(update_playhead_rect, streams=[tap_stream_rect, time_play_stream_rect])

pn.Row(pn.Column(rect_patches * dmap_time_rect, wave_curve * dmap_time_wave), audio)

<IPython.core.display.Javascript object>

Row
    [0] Column
        [0] HoloViews(DynamicMap, height=75, sizing_mode='fixed', width=1000)
        [1] HoloViews(DynamicMap, height=200, sizing_mode='fixed', width=1000)
    [1] Audio(str, name='audio', sample_rate=22050, throttle=1000)